<a href="https://colab.research.google.com/github/chainSAW-crypto/IRGANs-Doc_ranking/blob/main/IRGAN_Dataset_creation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install pdfplumber langchain langchain_groq

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.8/42.8 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.2/60.2 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 51.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.9/124.9 kB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 73.0 MB/s eta 0:00:00


In [ ]:
import os
import pdfplumber
import json

def extract_text_from_pdf(pdf_path, pages_per_doc=5):
    with pdfplumber.open(pdf_path) as pdf:
        all_pages = [page.extract_text() for page in pdf.pages]

    # Split pages into chunks of 5
    chunks = []
    for i in range(0, len(all_pages), pages_per_doc):
        chunk = all_pages[i:i+pages_per_doc]
        chunks.append(" ".join(chunk))

    return chunks

pdf_folder = "/content/folder"
documents = {}

for filename in os.listdir(pdf_folder):
    if filename.endswith(".pdf"):
        base_id = filename.split(".")[0]
        pdf_path = os.path.join(pdf_folder, filename)

        # Get 5-page chunks
        text_chunks = extract_text_from_pdf(pdf_path)

        # Create unique IDs for each chunk
        for chunk_idx, chunk_text in enumerate(text_chunks):
            doc_id = f"{base_id}_part{chunk_idx}"
            documents[doc_id] = chunk_text

# Save to JSON
with open("documents.json", "w") as f:
    json.dump(documents, f, indent=2)

FileNotFoundError: [Errno 2] No such file or directory: '/content/folder'

In [ ]:
# Save to JSON
import json
import os

with open("documents.json", "w") as f:
    json.dump(documents, f)

In [ ]:
# # export saved document.json file

# from google.colab import files
# files.download('documents.json')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# load document.json from the files

# Check if the file exists before attempting to load it.
if os.path.exists('documents.json'):
    with open('documents.json', 'r') as f:
        try:
            data = json.load(f)
            print(data)  # Or perform other operations with the loaded data
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON: {e}")
else:
    print("documents.json file not found.")

{'https__www_part0': 'Bovine Medicine\nDiseases and Husbandry of Cattle\nSecond edition\nEdited by\nA.H. Andrews\nwith\nR.W. Blowey\nH. Boyd\nR.G. Eddy\nBlackwell\nScience  Bovine Medicine\nDiseases and Husbandry of Cattle\nSecond edition\nEdited by\nA.H. Andrews\nwith\nR.W. Blowey\nH. Boyd\nR.G. Eddy\nBlackwell\nScience © 2004 by Blackwell Science Ltd First published 1992 by Blackwell Science\na Blackwell Publishing Company Second edition published 2004 by Blackwell Publishing\nEditorial Offices: Library of Congress Cataloging-in-Publication Data\nBlackwell Science Ltd,9600 Garsington Road,Oxford OX4 Bovine medicine :diseases and busbandry of cattle / edited\n2DQ,UK by A.H.Andrews ...[et al.].\nTel:+44 (0)1865 776868 2nd ed.\nIowa State Press,a Blackwell Publishing Company,2121 p.cm.\nState Avenue,Ames Iowa 50014-8300 USA Includes bibliographical references (p.).\nTel:+1 515 292 0140 ISBN 0-632-05596-0 (alk.paper)\nBlackwell Science Asia Pty Ltd,550 Swanston Street, 1. Cattle–Diseases

In [ ]:
from google.colab import userdata
groq_api_key = userdata.get('groq_api_key')
llm = ChatGroq(
            groq_api_key=groq_api_key,  # Use the passed API key directly
            model="llama-3.3-70b-versatile",
            temperature=0.7
        )

In [ ]:
from langchain_groq import ChatGroq
from langchain_core.messages import AIMessage
import time
import random
from google.colab import userdata
import json

# List of available Groq models to rotate through
GROQ_MODELS = [
    "llama-3.1-8b-instant",
    "gemma2-9b-it",
    "llama-3.3-70b-versatile",
    "llama-3.2-1b-preview"
]

# Track rate limits per model (global state)
model_rate_track = {model: {"last_call": 0, "calls": 0} for model in GROQ_MODELS}

def get_next_model():
    """Select model with oldest last call time and under rate limits"""
    now = time.time()

    # Filter models that haven't hit limits
    available_models = [
        model for model, stats in model_rate_track.items()
        if now - stats["last_call"] > 60/stats.get("rpm", 30)  # Default 30 RPM
    ]

    if not available_models:
        # All models rate limited - sleep and return random
        time.sleep(10)
        return random.choice(GROQ_MODELS)

    # Return least recently used available model
    return min(available_models, key=lambda m: model_rate_track[m]["last_call"])

def generate_queries(document_text, n=3, groq_api_key=None, max_retries=3):
    """Generate queries with model rotation and rate limit handling"""
    for attempt in range(max_retries):
        try:
            model = get_next_model()

            # Update rate tracking
            model_rate_track[model]["last_call"] = time.time()
            model_rate_track[model]["calls"] += 1

            llm = ChatGroq(
                groq_api_key=groq_api_key,
                model=model,
                temperature=0.7
            )

            response = llm.invoke(
                f"Generate exactly {n} search queries this document answers. "
                f"Return one query per line without numbering:\n{document_text[:3000]}"
            )

            if isinstance(response, AIMessage):
                content = response.content
            else:
                content = str(response)

            queries = [q.strip() for q in content.split("\n") if q.strip()]
            return queries[:n]

        except Exception as e:
            print(f"Attempt {attempt+1} failed with {model}: {str(e)[:100]}")
            time.sleep(5 * (attempt + 1))  # Exponential backoff

    return []  # Return empty if all retries fail


# Usage
query_doc_pairs = []

with open("documents.json", "r") as f:
    documents = json.load(f)

groq_api_key = userdata.get('groq_api_key')

for doc_id, text in documents.items():
    queries = generate_queries(
        document_text=text,
        n=3,
        groq_api_key=groq_api_key
    )

    if queries:
        query_doc_pairs.extend([(q, doc_id, 1) for q in queries])

    # Optional: Add small delay between calls
    time.sleep(0.5)  # Adjust based on your rate limits


In [ ]:
# prompt: code to save and download query_doc_pairs

import json

# Save query_doc_pairs to a JSON file
with open("query_doc_pairs.json", "w") as f:
    json.dump(query_doc_pairs, f)

# Download the JSON file
from google.colab import files
files.download("query_doc_pairs.json")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
query_doc_pairs

[('Here are three search queries this document answers:',
  'https__www_part0',
  1),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part0',
  1),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part0',
  1),
 ('Factors affecting milk quality', 'https__www_part1', 1),
 ('Lameness in cattle', 'https__www_part1', 1),
 ('Major infectious diseases of cattle', 'https__www_part1', 1),
 ('list of contributors to bovine medicine book', 'https__www_part2', 1),
 ('veterinary medicine experts in the UK and USA', 'https__www_part2', 1),
 ('contributors to bovine medicine textbook with international expertise',
  'https__www_part2',
  1),
 ('Chapter 1', 'https__www_part3', 1),
 ('Calf Rearing', 'https__www_part3', 1),
 ('D.M. Allen', 'https__www_part3', 1),
 ('Can the herd be integrated with a sheep flock?', 'https__www_part4', 1),
 ('Are there arable crop residues that can be used to cheapen cow feeding?',
  'https__www_part4',
  1),
 (

In [1]:
!pip install rank_bm25

In [8]:
from rank_bm25 import BM25Okapi
import random

with open("documents.json", "r") as f:
    documents = json.load(f)

with open("query_doc_pairs.json", "r") as f:
    query_doc_pairs = json.load(f)


corpus = list(documents.values())
tokenized_corpus = [doc.split() for doc in corpus]
bm25 = BM25Okapi(tokenized_corpus)

# Step 2: For each query in `query_doc_pairs`, find hard negatives
labeled_data = []
for query, source_doc_id, relevance in query_doc_pairs:
    if relevance == 1:  # Only process positive pairs
        tokenized_query = query.split()
        scores = bm25.get_scores(tokenized_query)

        # Get top 3 relevant docs (excluding the source document)
        all_indices = list(range(len(corpus)))
        source_index = list(documents.keys()).index(source_doc_id)
        candidate_indices = [i for i in all_indices if i != source_index]

        # Sort and pick top 3 as positives (already labeled)
        sorted_indices = sorted(candidate_indices, key=lambda i: -scores[i])
        top_doc_indices = sorted_indices[:3]

        # Add existing positive labels (from `query_doc_pairs`)
        labeled_data.append((query, source_doc_id, 1))

        # Add new hard negatives (low BM25 scores)
        neg_indices = sorted_indices[-3:]  # Least relevant docs
        for idx in neg_indices:
            doc_id = list(documents.keys())[idx]
            labeled_data.append((query, doc_id, 0))


In [9]:
labeled_data

[('Here are three search queries this document answers:',
  'https__www_part0',
  1),
 ('Here are three search queries this document answers:',
  'https__www_part243',
  0),
 ('Here are three search queries this document answers:',
  'https__www_part244',
  0),
 ('Here are three search queries this document answers:',
  'https__www_part246',
  0),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part0',
  1),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part9',
  0),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part99',
  0),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part130',
  0),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part0',
  1),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part244',
  0),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part246

In [12]:
import json
from google.colab import files

# Save labeled_data to a JSON file
with open("labeled_data.json", "w") as f:
    json.dump(labeled_data, f)

# Download the JSON file
files.download("labeled_data.json")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>